# Import Libraries

In [1]:
import pandas as pd
import numpy as np
import ydata_profiling as pp
from pycaret.regression import *

# Variables to Set

In [2]:
data_file = 'regression_dataset.csv'
target_column = 'Price'

# Load/Transform Data

In [3]:
df = pd.read_csv(data_file)
df[target_column] = df[target_column].astype(float)
df.head()

Price               Type  Living_space  Rooms  Bedrooms  Bathrooms  \
0   7900.0  Mid-terrace house          40.0    2.0       NaN        1.0   
1   9900.0  Mid-terrace house          70.0    3.0       2.0        1.0   
2  10000.0    Single dwelling         208.0    8.0       NaN        NaN   
3  10500.0  Mid-terrace house         200.0    4.0       NaN        1.0   
4  12000.0   Special property          24.0    2.0       NaN        NaN   

   Floors  Year_built                   State  Garages  
0     1.0      1980.0         Rheinland-Pfalz      1.0  
1     1.0      1890.0          Sachsen-Anhalt      NaN  
2     2.0      1920.0  Mecklenburg-Vorpommern      NaN  
3     2.0      1946.0          Sachsen-Anhalt      NaN  
4     NaN      1985.0                 Sachsen      NaN

In [4]:
df.dtypes

Price           float64
Type             object
Living_space    float64
Rooms           float64
Bedrooms        float64
Bathrooms       float64
Floors          float64
Year_built      float64
State            object
Garages         float64
dtype: object

# Profile Data

In [5]:
pp.ProfileReport(df)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Split into Training/Test and Validation Data

In [8]:
data = df.sample(frac=0.75, random_state=786)
data_unseen = df.drop(data.index)

data.reset_index(drop=True, inplace=True)
data_unseen.reset_index(drop=True, inplace=True)

print('Data for Modeling: ' + str(data.shape))
print('Unseen Data For Predictions: ' + str(data_unseen.shape))

Data for Modeling: (7888, 10)
Unseen Data For Predictions: (2629, 10)


# Setup Dataset with Pycaret

In [11]:
reg = setup(data = data, 
            target = target_column , 
            session_id=123,
            # silent = True,
            verbose = True) 

# Compare Regression Models

In [12]:
compare_models(
#         include = ['lr']
        
        exclude = ['lightgbm']
)

GradientBoostingRegressor(random_state=123)

# Build a Linear Regression Model

In [18]:
lr = create_model('lr')
gbr = create_model('gbr')

# Tune Linear Regression Model

In [14]:
tuned_lr = tune_model(lr)

Fitting 10 folds for each of 2 candidates, totalling 20 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [15]:
print(tuned_lr)

LinearRegression(n_jobs=-1)


# Evaluate Linear Regression Model

In [20]:
evaluate_model(tuned_lr)

interactive(children=(ToggleButtons(description='Plot Type:', icons=('',), options=(('Pipeline Plot', 'pipelin…

# Predict on Test Dataset

In [21]:
predict_model(tuned_lr)

Type  Living_space  Rooms  Bedrooms  Bathrooms  Floors  \
550    Special property     40.000000    2.0       NaN        1.0     NaN   
4975             Duplex    355.000000   20.0       NaN        5.0     4.0   
6190  Mid-terrace house    235.000000    8.0       NaN        3.0     4.0   
5116    Single dwelling    160.000000    6.0       4.0        2.0     4.0   
2312             Duplex    280.000000    8.5       4.0        2.0     NaN   
...                 ...           ...    ...       ...        ...     ...   
4786             Duplex    269.000000   15.0       NaN        NaN     3.0   
7590  Multiple dwelling    154.970001    6.0       4.0        2.0     2.0   
6328             Duplex    180.000000   10.0       NaN        2.0     2.0   
1416             Duplex    380.000000   14.0       NaN        NaN     NaN   
6626  Mid-terrace house    245.000000    6.0       5.0        1.0     2.0   

      Year_built                State  Garages     Price  prediction_label  
550          NaN          Brandenburg      1.0   79000.0          295464.0  
4975      1886.0              Sachsen      2.0  295000.0          446808.0  
6190      1994.0               Bayern      1.0  890000.0         1005420.0  
5116      1983.0               Bayern      2.0  525000.0          814516.0  
2312      1935.0  Nordrhein-Westfalen      1.0  395000.0          534660.0  
...          ...                  ...      ...       ...               ...  
4786      1913.0              Sachsen      2.0  300000.0          203568.0  
7590      1950.0  Nordrhein-Westfalen      2.0  315000.0          359580.0  
6328      1910.0  Nordrhein-Westfalen      4.0  195000.0          235944.0  
1416      1898.0              Sachsen      4.0  290000.0          394012.0  
6626      2011.0  Nordrhein-Westfalen      1.0  695000.0          594628.0  

[2367 rows x 11 columns]

# Predict on Validation Data

In [24]:
unseen_predictions = predict_model(tuned_lr, data=data_unseen)
unseen_predictions.head(20)

Type  Living_space  Rooms  Bedrooms  Bathrooms  Floors  \
0   Mid-terrace house     70.000000    3.0       2.0        1.0     1.0   
1   Mid-terrace house     61.150002    2.0       1.0        1.0     2.0   
2   Mid-terrace house     70.000000    3.0       2.0        1.0     1.0   
3                 NaN     30.000000    1.0       NaN        NaN     1.0   
4              Duplex    183.000000   10.0       NaN        NaN     NaN   
5    Special property     20.000000    1.0       NaN        1.0     NaN   
6   Mid-terrace house    120.000000    4.0       3.0        1.0     1.0   
7     Single dwelling     80.000000    5.0       NaN        1.0     NaN   
8   Mid-terrace house     90.000000    5.0       NaN        NaN     2.0   
9    Special property     40.000000    2.0       NaN        1.0     NaN   
10  Mid-terrace house     50.000000    3.0       NaN        NaN     1.0   
11       Corner house    100.000000    5.0       NaN        1.0     2.0   
12  Mid-terrace house     72.000000    3.0       2.0        1.0     1.0   
13  Mid-terrace house     95.000000    3.0       1.0        1.0     2.0   
14  Mid-terrace house     60.000000    2.0       1.0        1.0     1.0   
15  Mid-terrace house    100.000000    5.0       3.0        1.0     2.0   
16             Duplex    150.000000    6.0       NaN        NaN     NaN   
17  Mid-terrace house    165.000000    7.0       4.0        2.0     2.0   
18          Farmhouse     90.000000    5.0       NaN        1.0     NaN   
19          Farmhouse    150.000000    8.0       6.0        1.0     2.0   

    Year_built                   State  Garages    Price  prediction_label  
0       1890.0          Sachsen-Anhalt      NaN   9900.0         -135308.0  
1          NaN          Sachsen-Anhalt      NaN  12000.0           29048.0  
2          NaN          Sachsen-Anhalt      NaN  13500.0          -55020.0  
3       1960.0          Sachsen-Anhalt      1.0  16000.0          -59772.0  
4       1929.0             Brandenburg      NaN  19500.0          318532.0  
5       2008.0          Sachsen-Anhalt      NaN  19900.0           74368.0  
6       1960.0                  Hessen      1.0  20000.0          345944.0  
7       1920.0                 Sachsen      1.0  25000.0          -40212.0  
8       1850.0                 Sachsen      NaN  27500.0          -44072.0  
9       1900.0             Brandenburg      1.0  28000.0          226728.0  
10      1880.0                 Sachsen      NaN  29000.0         -125060.0  
11      1880.0          Sachsen-Anhalt      3.0  29000.0          -83304.0  
12      1960.0  Mecklenburg-Vorpommern      NaN  29500.0           -4024.0  
13      1930.0          Sachsen-Anhalt      NaN  29500.0           46812.0  
14      1900.0          Sachsen-Anhalt      NaN  29500.0         -113612.0  
15      1900.0          Sachsen-Anhalt      1.0  29999.0          -39800.0  
16      1900.0  Mecklenburg-Vorpommern      NaN  30000.0           89288.0  
17      1900.0           Niedersachsen      1.0  30000.0          225096.0  
18      1924.0          Sachsen-Anhalt      1.0  30000.0          -93932.0  
19      1950.0         Rheinland-Pfalz      NaN  30310.0           74092.0

In [25]:
unseen_predictions[unseen_predictions['Type']=='Farmhouse']

Type  Living_space  Rooms  Bedrooms  Bathrooms  Floors  Year_built  \
18    Farmhouse     90.000000    5.0       NaN        1.0     NaN      1924.0   
19    Farmhouse    150.000000    8.0       6.0        1.0     2.0      1950.0   
26    Farmhouse    200.000000    8.0       NaN        NaN     3.0         NaN   
31    Farmhouse    110.000000    5.0       2.0        1.0     3.0      1900.0   
39    Farmhouse    100.000000    4.0       3.0        1.0     3.0         NaN   
...         ...           ...    ...       ...        ...     ...         ...   
2252  Farmhouse    164.750000    5.0       4.0        2.0     3.0      2001.0   
2312  Farmhouse    120.000000    5.0       NaN        1.0     4.0      1962.0   
2336  Farmhouse    170.000000    4.0       NaN        2.0     NaN         NaN   
2343  Farmhouse    129.199997    5.0       4.0        2.0     4.0         NaN   
2487  Farmhouse    160.000000    5.0       3.0        2.0     2.0      1920.0   

                    State  Garages      Price  prediction_label  
18         Sachsen-Anhalt      1.0    30000.0          -93932.0  
19        Rheinland-Pfalz      NaN    30310.0           74092.0  
26              Thüringen      3.0    35000.0          231924.0  
31              Thüringen      2.0    38000.0           -5548.0  
39        Rheinland-Pfalz      NaN    39500.0          164860.0  
...                   ...      ...        ...               ...  
2252               Hessen      1.0   858600.0          578924.0  
2312               Bayern      1.0   960000.0          623764.0  
2336  Nordrhein-Westfalen      2.0   990000.0          422760.0  
2343               Bayern      2.0   995000.0          688700.0  
2487               Berlin      NaN  1490000.0          877008.0  

[163 rows x 11 columns]

In [23]:
from pycaret.utils import check_metric
check_metric(unseen_predictions[target_column], unseen_predictions.Label, 'MAPE')

ImportError: cannot import name 'check_metric' from 'pycaret.utils' (C:\ProgramData\Anaconda3\lib\site-packages\pycaret\utils\__init__.py)